##### Copyright 2018 The TensorFlow Authors.


In [1]:
#@title Licensed under the Apache License, Version 2.0 (the "License");
# you may not use this file except in compliance with the License.
# You may obtain a copy of the License at
#
# https://www.apache.org/licenses/LICENSE-2.0
#
# Unless required by applicable law or agreed to in writing, software
# distributed under the License is distributed on an "AS IS" BASIS,
# WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
# See the License for the specific language governing permissions and
# limitations under the License.

# テキストを読み込む

<table class="tfo-notebook-buttons" align="left">
  <td><a target="_blank" href="https://www.tensorflow.org/tutorials/load_data/text"><img src="https://www.tensorflow.org/images/tf_logo_32px.png">TensorFlow.org で表示</a></td>
  <td>     <a target="_blank" href="https://colab.research.google.com/github/tensorflow/docs-l10n/blob/master/site/ja/tutorials/load_data/text.ipynb"><img src="https://www.tensorflow.org/images/colab_logo_32px.png">Google Colab で実行</a>   </td>
  <td>     <a target="_blank" href="https://github.com/tensorflow/docs-l10n/blob/master/site/ja/tutorials/load_data/text.ipynb"><img src="https://www.tensorflow.org/images/GitHub-Mark-32px.png">GitHub でソースを表示</a>   </td>
  <td>     <a href="https://storage.googleapis.com/tensorflow_docs/docs-l10n/site/ja/tutorials/load_data/text.ipynb"><img src="https://www.tensorflow.org/images/download_logo_32px.png">ノートブックをダウンロード</a>   </td>
</table>

このチュートリアルでは、テキストを読み込んで前処理する 2 つの方法を紹介します。

- まず、Keras ユーティリティと前処理レイヤーを使用します。これには、データを `tf.data.Dataset` に変換するための `tf.keras.utils.text_dataset_from_directory` とデータを標準化、トークン化、およびベクトル化するための `tf.keras.layers.TextVectorization` が含まれます。TensorFlow を初めて使用する場合は、これらから始める必要があります。
- 次に、`tf.data.TextLineDataset` などの低レベルのユーティリティを使用してテキストファイルを読み込み、`text.UnicodeScriptTokenizer` や `text.case_fold_utf8` などの [TensorFlow Text](https://www.tensorflow.org/text)  APIを使用して、よりきめ細かい制御のためにデータを前処理します。

In [2]:
!pip install "tensorflow-text==2.8.*"

  Attempting uninstall: tensorflow-estimator
    Found existing installation: tensorflow-estimator 2.11.0


    Uninstalling tensorflow-estimator-2.11.0:
      Successfully uninstalled tensorflow-estimator-2.11.0


  Attempting uninstall: keras
    Found existing installation: keras 2.11.0


    Uninstalling keras-2.11.0:
      Successfully uninstalled keras-2.11.0


  Attempting uninstall: tensorboard
    Found existing installation: tensorboard 2.11.0


    Uninstalling tensorboard-2.11.0:
      Successfully uninstalled tensorboard-2.11.0


  Attempting uninstall: tensorflow
    Found existing installation: tensorflow 2.11.0


    Uninstalling tensorflow-2.11.0:


      Successfully uninstalled tensorflow-2.11.0


In [3]:
import collections
import pathlib

import tensorflow as tf

from tensorflow.keras import layers
from tensorflow.keras import losses
from tensorflow.keras import utils
from tensorflow.keras.layers import TextVectorization

import tensorflow_datasets as tfds
import tensorflow_text as tf_text

## 例 1: StackOverflow の質問のタグを予測する

最初の例として、StackOverflow からプログラミングの質問のデータセットをダウンロードします。それぞれの質問 (「ディクショナリを値で並べ替えるにはどうすればよいですか？」) は、1 つのタグ (<code>Python</code>、`CSharp`、`JavaScript`、または`Java`) でラベルされています。このタスクでは、質問のタグを予測するモデルを開発します。これは、マルチクラス分類の例です。マルチクラス分類は、重要で広く適用できる機械学習の問題です。

### データセットをダウンロードして調査する

まず、`tf.keras.utils.get_file` を使用して Stack Overflow データセットをダウンロードし、ディレクトリの構造を調べます。

In [4]:
data_url = 'https://storage.googleapis.com/download.tensorflow.org/data/stack_overflow_16k.tar.gz'

dataset_dir = utils.get_file(
    origin=data_url,
    untar=True,
    cache_dir='stack_overflow',
    cache_subdir='')

dataset_dir = pathlib.Path(dataset_dir).parent

  16384/6053168 [..............................] - ETA: 0s

6053888/6053168 [==============================] - 0s 0us/step


6062080/6053168 [==============================] - 0s 0us/step


In [5]:
list(dataset_dir.iterdir())

[PosixPath('/tmp/.keras/test'),
 PosixPath('/tmp/.keras/train'),
 PosixPath('/tmp/.keras/README.md'),
 PosixPath('/tmp/.keras/stack_overflow_16k.tar.gz')]

In [6]:
train_dir = dataset_dir/'train'
list(train_dir.iterdir())

[PosixPath('/tmp/.keras/train/csharp'),
 PosixPath('/tmp/.keras/train/javascript'),
 PosixPath('/tmp/.keras/train/python'),
 PosixPath('/tmp/.keras/train/java')]

`train/csharp`、`train/java`、`train/python` および `train/javascript` ディレクトリには、多くのテキストファイルが含まれています。それぞれが Stack Overflow の質問です。

サンプルファイルを出力してデータを調べます。

In [7]:
sample_file = train_dir/'python/1755.txt'

with open(sample_file) as f:
  print(f.read())

why does this blank program print true x=true.def stupid():.    x=false.stupid().print x



### データセットを読み込む

次に、データをディスクから読み込み、トレーニングに適した形式に準備します。これを行うには、`tf.keras.utils.text_dataset_from_directory` ユーティリティを使用して、ラベル付きの `tf.data.Dataset` を作成します。これは、入力パイプラインを構築するための強力なツールのコレクションです。`tf.data` を始めて使用する場合は、[tf.data: TensorFlow 入力パイプラインを構築する](../../guide/data.ipynb)を参照してください。

`tf.keras.utils.text_dataset_from_directory` API は、次のようなディレクトリ構造を想定しています。

```
train/
...csharp/
......1.txt
......2.txt
...java/
......1.txt
......2.txt
...javascript/
......1.txt
......2.txt
...python/
......1.txt
......2.txt
```

機械学習実験を実行するときは、データセットを[トレーニング](https://developers.google.com/machine-learning/glossary#training_set)、[検証](https://developers.google.com/machine-learning/glossary#validation_set)、および、[テスト](https://developers.google.com/machine-learning/glossary#test-set)の 3 つに分割することをお勧めします。

Stack Overflow データセットは、すでにトレーニングセットとテストセットに分割されていますが、検証セットはありません。

`tf.keras.utils.text_dataset_from_directory` を使用し、`validation_split` を `0.2` (20%) に設定し、トレーニングデータを 80:20 に分割して検証セットを作成します。

In [8]:
batch_size = 32
seed = 42

raw_train_ds = utils.text_dataset_from_directory(
    train_dir,
    batch_size=batch_size,
    validation_split=0.2,
    subset='training',
    seed=seed)

Found 8000 files belonging to 4 classes.
Using 6400 files for training.


前のセル出力が示すように、トレーニングフォルダには 8,000 の例があり、そのうち 80％ (6,400) をトレーニングに使用します。`tf.data.Dataset` を `Model.fit` に直接渡すことで、モデルをトレーニングできます。詳細は、後ほど見ていきます。

まず、データセットを反復処理し、いくつかの例を出力して、データを確認します。

注意: 分類問題の難易度を上げるために、データセットの作成者は、プログラミングの質問で、*Python*、*CSharp*、*JavaScript*、*Java* という単語を *blank* に置き換えました。

In [9]:
for text_batch, label_batch in raw_train_ds.take(1):
  for i in range(10):
    print("Question: ", text_batch.numpy()[i])
    print("Label:", label_batch.numpy()[i])

Question:  b'"my tester is going to the wrong constructor i am new to programming so if i ask a question that can be easily fixed, please forgive me. my program has a tester class with a main. when i send that to my regularpolygon class, it sends it to the wrong constructor. i have two constructors. 1 without perameters..public regularpolygon().    {.       mynumsides = 5;.       mysidelength = 30;.    }//end default constructor...and my second, with perameters. ..public regularpolygon(int numsides, double sidelength).    {.        mynumsides = numsides;.        mysidelength = sidelength;.    }// end constructor...in my tester class i have these two lines:..regularpolygon shape = new regularpolygon(numsides, sidelength);.        shape.menu();...numsides and sidelength were declared and initialized earlier in the testing class...so what i want to happen, is the tester class sends numsides and sidelength to the second constructor and use it in that class. but it only uses the default con

ラベルは、`0`、`1`、`2` または `3` です。これらのどれがどの文字列ラベルに対応するかを確認するには、データセットの `class_names` プロパティを確認します。


In [10]:
for i, label in enumerate(raw_train_ds.class_names):
  print("Label", i, "corresponds to", label)

Label 0 corresponds to csharp
Label 1 corresponds to java
Label 2 corresponds to javascript
Label 3 corresponds to python


次に、`tf.keras.utils.text_dataset_from_directory` を使って検証およびテスト用データセットを作成します。トレーニング用セットの残りの 1,600 件のレビューを検証に使用します。

注意:  `tf.keras.utils.text_dataset_from_directory` の `validation_split` および `subset` 引数を使用する場合は、必ずランダムシードを指定するか、`shuffle=False`を渡して、検証とトレーニング分割に重複がないようにします。

In [11]:
# Create a validation set.
raw_val_ds = utils.text_dataset_from_directory(
    train_dir,
    batch_size=batch_size,
    validation_split=0.2,
    subset='validation',
    seed=seed)

Found 8000 files belonging to 4 classes.
Using 1600 files for validation.


In [12]:
test_dir = dataset_dir/'test'

# Create a test set.
raw_test_ds = utils.text_dataset_from_directory(
    test_dir,
    batch_size=batch_size)

Found 8000 files belonging to 4 classes.


### トレーニング用データセットを準備する

次に、`tf.keras.layers.TextVectorization` レイヤーを使用して、データを標準化、トークン化、およびベクトル化します。

- 標準化とは、テキストを前処理することを指します。通常、句読点や HTML 要素を削除して、データセットを簡素化します。
- トークン化とは、文字列をトークンに分割することです（たとえば、空白で分割することにより、文を個々の単語に分割します）。
- ベクトル化とは、トークンを数値に変換して、ニューラルネットワークに入力できるようにすることです。

これらのタスクはすべて、このレイヤーで実行できます。これらの詳細については、`tf.keras.layers.TextVectorization` API ドキュメントを参照してください。

注意点 :

- デフォルトの標準化では、テキストが小文字に変換され、句読点が削除されます (`standardize='lower_and_strip_punctuation'`)。
- デフォルトのトークナイザーは空白で分割されます (`split='whitespace'`)。
- デフォルトのベクトル化モードは `int` です (`output_mode='int'`)。これは整数インデックスを出力します（トークンごとに1つ）。このモードは、語順を考慮したモデルを構築するために使用できます。`binary` などの他のモードを使用して、[bag-of-word](https://developers.google.com/machine-learning/glossary#bag-of-words) モデルを構築することもできます。

`TextVectorization` を使用した標準化、トークン化、およびベクトル化について詳しくみるために、2 つのモデルを作成します。

- まず、`'binary'` ベクトル化モードを使用して、bag-of-words モデルを構築します。
- 次に、1D ConvNet で `'int'` モードを使用します。

In [13]:
VOCAB_SIZE = 10000

binary_vectorize_layer = TextVectorization(
    max_tokens=VOCAB_SIZE,
    output_mode='binary')

`'int'` モードの場合、最大語彙サイズに加えて、明示的な最大シーケンス長 (`MAX_SEQUENCE_LENGTH`) を設定する必要があります。これにより、レイヤーはシーケンスを正確に `output_sequence_length` 値にパディングまたは切り捨てます。

In [14]:
MAX_SEQUENCE_LENGTH = 250

int_vectorize_layer = TextVectorization(
    max_tokens=VOCAB_SIZE,
    output_mode='int',
    output_sequence_length=MAX_SEQUENCE_LENGTH)

次に、`TextVectorization.adapt` を呼び出して、前処理レイヤーの状態をデータセットに適合させます。これにより、モデルは文字列から整数へのインデックスを作成します。

注意: `TextVectorization.adapt` を呼び出すときは、トレーニング用データのみを使用することが重要です (テスト用セットを使用すると情報が漏洩します)。

In [15]:
# Make a text-only dataset (without labels), then call `TextVectorization.adapt`.
train_text = raw_train_ds.map(lambda text, labels: text)
binary_vectorize_layer.adapt(train_text)
int_vectorize_layer.adapt(train_text)

これらのレイヤーを使用してデータを前処理した結果を出力します。

In [16]:
def binary_vectorize_text(text, label):
  text = tf.expand_dims(text, -1)
  return binary_vectorize_layer(text), label

In [17]:
def int_vectorize_text(text, label):
  text = tf.expand_dims(text, -1)
  return int_vectorize_layer(text), label

In [18]:
# Retrieve a batch (of 32 reviews and labels) from the dataset.
text_batch, label_batch = next(iter(raw_train_ds))
first_question, first_label = text_batch[0], label_batch[0]
print("Question", first_question)
print("Label", first_label)

Question tf.Tensor(b'"what is the difference between these two ways to create an element? var a = document.createelement(\'div\');..a.id = ""mydiv"";...and..var a = document.createelement(\'div\').id = ""mydiv"";...what is the difference between them such that the first one works and the second one doesn\'t?"\n', shape=(), dtype=string)
Label tf.Tensor(2, shape=(), dtype=int32)


In [19]:
print("'binary' vectorized question:",
      binary_vectorize_text(first_question, first_label)[0])

'binary' vectorized question: tf.Tensor([[1. 1. 0. ... 0. 0. 0.]], shape=(1, 10000), dtype=float32)


In [20]:
print("'int' vectorized question:",
      int_vectorize_text(first_question, first_label)[0])

'int' vectorized question: tf.Tensor(
[[ 55   6   2 410 211 229 121 895   4 124  32 245  43   5   1   1   5   1
    1   6   2 410 211 191 318  14   2  98  71 188   8   2 199  71 178   0
    0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0


上に示したように、`TextVectorization` の `'binary'` モードは、入力に少なくとも 1 回存在するトークンを示す配列を返しますが、`'int'` モードでは、各トークンが整数に置き換えられるため、トークンの順序が保持されます。

レイヤーで `TextVectorization.get_vocabulary` を呼び出すことにより、各整数が対応するトークン (文字列) を検索できます。

In [21]:
print("1289 ---> ", int_vectorize_layer.get_vocabulary()[1289])
print("313 ---> ", int_vectorize_layer.get_vocabulary()[313])
print("Vocabulary size: {}".format(len(int_vectorize_layer.get_vocabulary())))

1289 --->  roman
313 --->  source
Vocabulary size: 10000


モデルをトレーニングする準備がほぼ整いました。

最後の前処理ステップとして、トレーニング、検証、およびデータセットのテストのために前に作成した `TextVectorization` レイヤーを適用します。

In [22]:
binary_train_ds = raw_train_ds.map(binary_vectorize_text)
binary_val_ds = raw_val_ds.map(binary_vectorize_text)
binary_test_ds = raw_test_ds.map(binary_vectorize_text)

int_train_ds = raw_train_ds.map(int_vectorize_text)
int_val_ds = raw_val_ds.map(int_vectorize_text)
int_test_ds = raw_test_ds.map(int_vectorize_text)

### パフォーマンスのためにデータセットを構成する

以下は、データを読み込むときに I/O がブロックされないようにするために使用する必要がある 2 つの重要な方法です。

- `Dataset.cache` はデータをディスクから読み込んだ後、データをメモリに保持します。これにより、モデルのトレーニング中にデータセットがボトルネックになることを回避できます。データセットが大きすぎてメモリに収まらない場合は、この方法を使用して、パフォーマンスの高いオンディスクキャッシュを作成することもできます。これは、多くの小さなファイルを読み込むより効率的です。
- `Dataset.prefetch` はトレーニング中にデータの前処理とモデルの実行をオーバーラップさせます。

以上の 2 つの方法とデータをディスクにキャッシュする方法についての詳細は、<a>データパフォーマンスガイド</a>の <em>プリフェッチ</em>を参照してください。

In [23]:
AUTOTUNE = tf.data.AUTOTUNE

def configure_dataset(dataset):
  return dataset.cache().prefetch(buffer_size=AUTOTUNE)

In [24]:
binary_train_ds = configure_dataset(binary_train_ds)
binary_val_ds = configure_dataset(binary_val_ds)
binary_test_ds = configure_dataset(binary_test_ds)

int_train_ds = configure_dataset(int_train_ds)
int_val_ds = configure_dataset(int_val_ds)
int_test_ds = configure_dataset(int_test_ds)

### モデルをトレーニングする

ニューラルネットワークを作成します。

`'binary'` のベクトル化されたデータの場合、単純な bag-of-words 線形モデルを定義し、それを構成してトレーニングします。

In [25]:
binary_model = tf.keras.Sequential([layers.Dense(4)])

binary_model.compile(
    loss=losses.SparseCategoricalCrossentropy(from_logits=True),
    optimizer='adam',
    metrics=['accuracy'])

history = binary_model.fit(
    binary_train_ds, validation_data=binary_val_ds, epochs=10)

Epoch 1/10


  1/200 [..............................] - ETA: 2:25 - loss: 1.3763 - accuracy: 0.2188

 18/200 [=>............................] - ETA: 0s - loss: 1.3713 - accuracy: 0.2743  

 36/200 [====>.........................] - ETA: 0s - loss: 1.3472 - accuracy: 0.3628

 54/200 [=======>......................] - ETA: 0s - loss: 1.3138 - accuracy: 0.4427

...

122/200 [=================>............] - ETA: 0s - loss: 0.2994 - accuracy: 0.9454

146/200 [====================>.........] - ETA: 0s - loss: 0.2976 - accuracy: 0.9461

170/200 [========================>.....] - ETA: 0s - loss: 0.2948 - accuracy: 0.9472

194/200 [============================>.] - ETA: 0s - loss: 0.2936 - accuracy: 0.9485

200/200 [==============================] - 1s 3ms/step - loss: 0.2923 - accuracy: 0.9486 - val_loss: 0.4908 - val_accuracy: 0.8413


次に、`'int'` ベクトル化レイヤーを使用して、1D ConvNet を構築します。

In [26]:
def create_model(vocab_size, num_labels):
  model = tf.keras.Sequential([
      layers.Embedding(vocab_size, 64, mask_zero=True),
      layers.Conv1D(64, 5, padding="valid", activation="relu", strides=2),
      layers.GlobalMaxPooling1D(),
      layers.Dense(num_labels)
  ])
  return model

In [27]:
# `vocab_size` is `VOCAB_SIZE + 1` since `0` is used additionally for padding.
int_model = create_model(vocab_size=VOCAB_SIZE + 1, num_labels=4)
int_model.compile(
    loss=losses.SparseCategoricalCrossentropy(from_logits=True),
    optimizer='adam',
    metrics=['accuracy'])
history = int_model.fit(int_train_ds, validation_data=int_val_ds, epochs=5)

Epoch 1/5


  1/200 [..............................] - ETA: 4:40 - loss: 1.3860 - accuracy: 0.2812

 17/200 [=>............................] - ETA: 0s - loss: 1.3862 - accuracy: 0.2592  

 34/200 [====>.........................] - ETA: 0s - loss: 1.3819 - accuracy: 0.2711

 51/200 [======>.......................] - ETA: 0s - loss: 1.3747 - accuracy: 0.3156

...

137/200 [===================>..........] - ETA: 0s - loss: 0.1219 - accuracy: 0.9781

154/200 [======================>.......] - ETA: 0s - loss: 0.1187 - accuracy: 0.9793

171/200 [========================>.....] - ETA: 0s - loss: 0.1164 - accuracy: 0.9793

188/200 [===========================>..] - ETA: 0s - loss: 0.1131 - accuracy: 0.9799

200/200 [==============================] - 1s 4ms/step - loss: 0.1108 - accuracy: 0.9805 - val_loss: 0.5063 - val_accuracy: 0.8181


2 つのモデルを比較します。

In [28]:
print("Linear model on binary vectorized data:")
print(binary_model.summary())

Linear model on binary vectorized data:
Model: "sequential"


_________________________________________________________________


 Layer (type)                Output Shape              Param #   


 dense (Dense)               (None, 4)                 40004     


Total params: 40,004


Trainable params: 40,004


Non-trainable params: 0


_________________________________________________________________


None


In [29]:
print("ConvNet model on int vectorized data:")
print(int_model.summary())

ConvNet model on int vectorized data:
Model: "sequential_1"


_________________________________________________________________


 Layer (type)                Output Shape              Param #   


 embedding (Embedding)       (None, None, 64)          640064    


 conv1d (Conv1D)             (None, None, 64)          20544     


...

Total params: 660,868


Trainable params: 660,868


Non-trainable params: 0


_________________________________________________________________


None


テストデータで両方のモデルを評価します。

In [30]:
binary_loss, binary_accuracy = binary_model.evaluate(binary_test_ds)
int_loss, int_accuracy = int_model.evaluate(int_test_ds)

print("Binary model accuracy: {:2.2%}".format(binary_accuracy))
print("Int model accuracy: {:2.2%}".format(int_accuracy))

  1/250 [..............................] - ETA: 19s - loss: 0.5814 - accuracy: 0.8125

 19/250 [=>............................] - ETA: 0s - loss: 0.5146 - accuracy: 0.8158 

 37/250 [===>..........................] - ETA: 0s - loss: 0.5115 - accuracy: 0.8209

 56/250 [=====>........................] - ETA: 0s - loss: 0.5176 - accuracy: 0.8203

 74/250 [=======>......................] - ETA: 0s - loss: 0.5223 - accuracy: 0.8180

...

194/250 [======================>.......] - ETA: 0s - loss: 0.5286 - accuracy: 0.8082

218/250 [=========================>....] - ETA: 0s - loss: 0.5318 - accuracy: 0.8048

242/250 [============================>.] - ETA: 0s - loss: 0.5252 - accuracy: 0.8073

250/250 [==============================] - 1s 2ms/step - loss: 0.5244 - accuracy: 0.8070


Binary model accuracy: 81.48%
Int model accuracy: 80.70%


注意: このサンプルデータセットは、かなり単純な分類問題を表しています。より複雑なデータセットと問題は、前処理戦略とモデルアーキテクチャに微妙ながら重要な違いをもたらします。さまざまなアプローチを比較するために、さまざまなハイパーパラメータとエポックを試してみてください。

### モデルをエクスポートする

上記のコードでは、モデルにテキストをフィードする前に、`tf.keras.layers.TextVectorization` レイヤーをデータセットに適用しました。モデルで生の文字列を処理できるようにする場合 (たとえば、展開を簡素化するため)、モデル内に `TextVectorization` レイヤーを含めることができます。

これを行うには、トレーニングしたばかりの重みを使用して新しいモデルを作成できます。

In [31]:
export_model = tf.keras.Sequential(
    [binary_vectorize_layer, binary_model,
     layers.Activation('sigmoid')])

export_model.compile(
    loss=losses.SparseCategoricalCrossentropy(from_logits=False),
    optimizer='adam',
    metrics=['accuracy'])

# Test it with `raw_test_ds`, which yields raw strings
loss, accuracy = export_model.evaluate(raw_test_ds)
print("Accuracy: {:2.2%}".format(binary_accuracy))

  1/250 [..............................] - ETA: 55s - loss: 0.4487 - accuracy: 0.9375

 12/250 [>.............................] - ETA: 1s - loss: 0.5282 - accuracy: 0.8021 

 24/250 [=>............................] - ETA: 1s - loss: 0.5292 - accuracy: 0.8047

 36/250 [===>..........................] - ETA: 0s - loss: 0.5131 - accuracy: 0.8177

 48/250 [====>.........................] - ETA: 0s - loss: 0.5053 - accuracy: 0.8197

...

222/250 [=========================>....] - ETA: 0s - loss: 0.5164 - accuracy: 0.8149

234/250 [===========================>..] - ETA: 0s - loss: 0.5182 - accuracy: 0.8132

247/250 [============================>.] - ETA: 0s - loss: 0.5164 - accuracy: 0.8145

250/250 [==============================] - 1s 4ms/step - loss: 0.5173 - accuracy: 0.8148


Accuracy: 81.48%


これで、モデルは生の文字列を入力として受け取り、`Model.predict` を使用して各ラベルのスコアを予測できます。最大スコアのラベルを見つける関数を定義します。

In [32]:
def get_string_labels(predicted_scores_batch):
  predicted_int_labels = tf.math.argmax(predicted_scores_batch, axis=1)
  predicted_labels = tf.gather(raw_train_ds.class_names, predicted_int_labels)
  return predicted_labels

### 新しいデータで推論を実行する

In [33]:
inputs = [
    "how do I extract keys from a dict into a list?",  # 'python'
    "debug public static void main(string[] args) {...}",  # 'java'
]
predicted_scores = export_model.predict(inputs)
predicted_labels = get_string_labels(predicted_scores)
for input, label in zip(inputs, predicted_labels):
  print("Question: ", input)
  print("Predicted label: ", label.numpy())

Question:  how do I extract keys from a dict into a list?
Predicted label:  b'python'
Question:  debug public static void main(string[] args) {...}
Predicted label:  b'java'


モデル内にテキスト前処理ロジックを含めると、モデルを本番環境にエクスポートして展開を簡素化し、[トレーニング/テストスキュー](https://developers.google.com/machine-learning/guides/rules-of-ml#training-serving_skew)の可能性を減らすことができます。

`tf.keras.layers.TextVectorization` を適用する場所を選択する際に性能の違いに留意する必要があります。モデルの外部で使用すると、GPU でトレーニングするときに非同期 CPU 処理とデータのバッファリングを行うことができます。したがって、GPU でモデルをトレーニングしている場合は、モデルの開発中に最高のパフォーマンスを得るためにこのオプションを使用し、デプロイの準備ができたらモデル内に `TextVectorization` レイヤーを含めるように切り替えることをお勧めします。

モデルの保存の詳細については、[モデルの保存と読み込み](../keras/save_and_load.ipynb)チュートリアルをご覧ください。

## 例 2: イーリアスの翻訳者を予測する


以下に、`tf.data.TextLineDataset` を使用してテキストファイルから例を読み込み、[TensorFlow Text](https://www.tensorflow.org/text) を使用してデータを前処理する例を示します。この例では、ホーマーのイーリアスの 3 つの異なる英語翻訳を使用し、与えられた 1 行のテキストから翻訳者を識別するようにモデルをトレーニングします。

### データセットをダウンロードして調査する

3 つのテキストの翻訳者は次のとおりです。

- [ウィリアム・クーパー](https://en.wikipedia.org/wiki/William_Cowper) — [テキスト](https://storage.googleapis.com/download.tensorflow.org/data/illiad/cowper.txt)
- [エドワード、ダービー伯爵](https://en.wikipedia.org/wiki/Edward_Smith-Stanley,_14th_Earl_of_Derby) — [テキスト](https://storage.googleapis.com/download.tensorflow.org/data/illiad/derby.txt)
- [サミュエル・バトラー](https://en.wikipedia.org/wiki/Samuel_Butler_%28novelist%29) — [テキスト](https://storage.googleapis.com/download.tensorflow.org/data/illiad/butler.txt)

このチュートリアルで使われているテキストファイルは、ヘッダ、フッタ、行番号、章のタイトルの削除など、いくつかの典型的な前処理が行われています。

前処理後のファイルをローカルにダウンロードします。

In [34]:
DIRECTORY_URL = 'https://storage.googleapis.com/download.tensorflow.org/data/illiad/'
FILE_NAMES = ['cowper.txt', 'derby.txt', 'butler.txt']

for name in FILE_NAMES:
  text_dir = utils.get_file(name, origin=DIRECTORY_URL + name)

parent_dir = pathlib.Path(text_dir).parent
list(parent_dir.iterdir())

 16384/815980 [..............................] - ETA: 0s

819200/815980 [==============================] - 0s 0us/step


827392/815980 [==============================] - 0s 0us/step


 16384/809730 [..............................] - ETA: 0s

811008/809730 [==============================] - 0s 0us/step


819200/809730 [==============================] - 0s 0us/step


 16384/807992 [..............................] - ETA: 0s

811008/807992 [==============================] - 0s 0us/step


819200/807992 [==============================] - 0s 0us/step


[PosixPath('/home/kbuilder/.keras/datasets/194px-New_East_River_Bridge_from_Brooklyn_det.4a09796u.jpg'),
 PosixPath('/home/kbuilder/.keras/datasets/spa-eng'),
 PosixPath('/home/kbuilder/.keras/datasets/jena_climate_2009_2016.csv'),
 PosixPath('/home/kbuilder/.keras/datasets/facades'),
 PosixPath('/home/kbuilder/.keras/datasets/mnist.npz'),
 PosixPath('/home/kbuilder/.keras/datasets/flower_photos.tar.gz'),
 PosixPath('/home/kbuilder/.keras/datasets/kandinsky5.jpg'),
 PosixPath('/home/kbuilder/.keras/datasets/heart.csv'),
 PosixPath('/home/kbuilder/.keras/datasets/ImageNetLabels.txt'),
 PosixPath('/home/kbuilder/.keras/datasets/jena_climate_2009_2016.csv.zip'),
 PosixPath('/home/kbuilder/.keras/datasets/320px-Felis_catus-cat_on_snow.jpg'),
 PosixPath('/home/kbuilder/.keras/datasets/Giant Panda'),
 PosixPath('/home/kbuilder/.keras/datasets/flower_photos'),
 PosixPath('/home/kbuilder/.keras/datasets/shakespeare.txt'),
 PosixPath('/home/kbuilder/.keras/datasets/facades.tar.gz'),
 PosixPath(

### データセットを読み込む

以前は、`tf.keras.utils.text_dataset_from_directory` では、ファイルのすべてのコンテンツが 1 つの例として扱われていました。ここでは、`tf.data.TextLineDataset` を使用します。これは、テキストファイルから `tf.data.Dataset` を作成するように設計されています。それぞれの例は、元のファイルからの行です。`TextLineDataset` は、主に行ベースのテキストデータ  (詩やエラーログなど) に役立ちます。

これらのファイルを繰り返し処理し、各ファイルを独自のデータセットに読み込みます。各例には個別にラベルを付ける必要があるため、`Dataset.map` を使用して、それぞれにラベラー関数を適用します。これにより、データセット内のすべての例が繰り返され、 (`example, label`) ペアが返されます。

In [35]:
def labeler(example, index):
  return example, tf.cast(index, tf.int64)

In [36]:
labeled_data_sets = []

for i, file_name in enumerate(FILE_NAMES):
  lines_dataset = tf.data.TextLineDataset(str(parent_dir/file_name))
  labeled_dataset = lines_dataset.map(lambda ex: labeler(ex, i))
  labeled_data_sets.append(labeled_dataset)

次に、`Dataset.concatenate` を使用し、これらのラベル付きデータセットを 1 つのデータセットに結合し、`Dataset.shuffle` を使用してシャッフルします。


In [37]:
BUFFER_SIZE = 50000
BATCH_SIZE = 64
VALIDATION_SIZE = 5000

In [38]:
all_labeled_data = labeled_data_sets[0]
for labeled_dataset in labeled_data_sets[1:]:
  all_labeled_data = all_labeled_data.concatenate(labeled_dataset)

all_labeled_data = all_labeled_data.shuffle(
    BUFFER_SIZE, reshuffle_each_iteration=False)

前述の手順でいくつかの例を出力します。データセットはまだバッチ処理されていないため、`all_labeled_data` の各エントリは 1 つのデータポイントに対応します。

In [39]:
for text, label in all_labeled_data.take(10):
  print("Sentence: ", text.numpy())
  print("Label:", label.numpy())

Sentence:  b"the man's right shoulder, and then stuck in the ground. He stood stock"
Label: 2
Sentence:  b'For yet a child he left me, when he fell'
Label: 1
Sentence:  b'Save me, my brother! Pity me! Thy steeds'
Label: 0
Sentence:  b'prepared the mess she bade them drink it. When they had done so and had'
Label: 2
Sentence:  b'exhorts him to return to the field of battle. An interview succeeds'
Label: 0
Sentence:  b'Then said Achilles, "Son of Atreus, king of men Agamemnon, see to these'
Label: 2
Sentence:  b'The hand of Menelaus, and while all'
Label: 0
Sentence:  b"A huge bull's hide, all drench'd and soak'd with grease;"
Label: 1
Sentence:  b'He sat, where sat the other Powers divine,'
Label: 0
Sentence:  b'And in my cause lies slain, of any Greek'
Label: 1


### トレーニング用データセットを準備する

`tf.keras.layers.TextVectorization` を使用してテキストデータセットを前処理する代わりに、TensorFlow Text API を使用してデータを標準化およびトークン化し、語彙を作成し、`tf.lookup.StaticVocabularyTable` を使用してトークンを整数にマッピングし、モデルにフィードします。(詳細については [TensorFlow Text](https://www.tensorflow.org/text) を参照してください)。

テキストを小文字に変換してトークン化する関数を定義します。

- TensorFlow Text は、さまざまなトークナイザーを提供します。この例では、`text.UnicodeScriptTokenizer` を使用してデータセットをトークン化します。
- `Dataset.map` を使用して、トークン化をデータセットに適用します。

In [40]:
tokenizer = tf_text.UnicodeScriptTokenizer()

In [41]:
def tokenize(text, unused_label):
  lower_case = tf_text.case_fold_utf8(text)
  return tokenizer.tokenize(lower_case)

In [42]:
tokenized_ds = all_labeled_data.map(tokenize)

データセットを反復処理して、トークン化されたいくつかの例を出力します。


In [43]:
for text_batch in tokenized_ds.take(5):
  print("Tokens: ", text_batch.numpy())

Tokens:  [b'the' b'man' b"'" b's' b'right' b'shoulder' b',' b'and' b'then' b'stuck'
 b'in' b'the' b'ground' b'.' b'he' b'stood' b'stock']
Tokens:  [b'for' b'yet' b'a' b'child' b'he' b'left' b'me' b',' b'when' b'he'
 b'fell']
Tokens:  [b'save' b'me' b',' b'my' b'brother' b'!' b'pity' b'me' b'!' b'thy'
 b'steeds']
Tokens:  [b'prepared' b'the' b'mess' b'she' b'bade' b'them' b'drink' b'it' b'.'
 b'when' b'they' b'had' b'done' b'so' b'and' b'had']
Tokens:  [b'exhorts' b'him' b'to' b'return' b'to' b'the' b'field' b'of' b'battle'
 b'.' b'an' b'interview' b'succeeds']


次に、トークンを頻度で並べ替え、上位の `VOCAB_SIZE` トークンを保持することにより、語彙を構築します。

In [44]:
tokenized_ds = configure_dataset(tokenized_ds)

vocab_dict = collections.defaultdict(lambda: 0)
for toks in tokenized_ds.as_numpy_iterator():
  for tok in toks:
    vocab_dict[tok] += 1

vocab = sorted(vocab_dict.items(), key=lambda x: x[1], reverse=True)
vocab = [token for token, count in vocab]
vocab = vocab[:VOCAB_SIZE]
vocab_size = len(vocab)
print("Vocab size: ", vocab_size)
print("First five vocab entries:", vocab[:5])

Vocab size:  10000
First five vocab entries: [b',', b'the', b'and', b"'", b'of']


トークンを整数に変換するには、`vocab` セットを使用して、`tf.lookup.StaticVocabularyTable` を作成します。トークンを [`2`, `vocab_size + 2`] の範囲の整数にマップします。`TextVectorization` レイヤーと同様に、`0` はパディングを示すために予約されており、`1` は語彙外 (OOV) トークンを示すために予約されています。

In [45]:
keys = vocab
values = range(2, len(vocab) + 2)  # Reserve `0` for padding, `1` for OOV tokens.

init = tf.lookup.KeyValueTensorInitializer(
    keys, values, key_dtype=tf.string, value_dtype=tf.int64)

num_oov_buckets = 1
vocab_table = tf.lookup.StaticVocabularyTable(init, num_oov_buckets)

最後に、トークナイザーとルックアップテーブルを使用して、データセットを標準化、トークン化、およびベクトル化する関数を定義します。

In [46]:
def preprocess_text(text, label):
  standardized = tf_text.case_fold_utf8(text)
  tokenized = tokenizer.tokenize(standardized)
  vectorized = vocab_table.lookup(tokenized)
  return vectorized, label

1 つの例でこれを試して、出力を確認します。

In [47]:
example_text, example_label = next(iter(all_labeled_data))
print("Sentence: ", example_text.numpy())
vectorized_text, example_label = preprocess_text(example_text, example_label)
print("Vectorized sentence: ", vectorized_text.numpy())

Sentence:  b"the man's right shoulder, and then stuck in the ground. He stood stock"
Vectorized sentence:  [   3   86    5   29  274  527    2    4   33 2749   13    3  191    7
   12  108 3286]


次に、`Dataset.map` を使用して、データセットに対して前処理関数を実行します。

In [48]:
all_encoded_data = all_labeled_data.map(preprocess_text)

### データセットをトレーニング用セットとテスト用セットに分割する


Keras `TextVectorization` レイヤーでも、ベクトル化されたデータをバッチ処理してパディングします。バッチ内の例は同じサイズと形状である必要があるため、パディングが必要です。これらのデータセットの例はすべて同じサイズではありません。テキストの各行には、異なる数の単語があります。

`tf.data.Dataset` は、データセットの分割とパディングのバッチ処理をサポートしています

In [49]:
train_data = all_encoded_data.skip(VALIDATION_SIZE).shuffle(BUFFER_SIZE)
validation_data = all_encoded_data.take(VALIDATION_SIZE)

In [50]:
train_data = train_data.padded_batch(BATCH_SIZE)
validation_data = validation_data.padded_batch(BATCH_SIZE)

`validation_data` および `train_data` は (`example, label`) ペアのコレクションではなく、バッチのコレクションです。各バッチは、配列として表される (*多くの例*、*多くのラベル*) のペアです。

以下に示します。

In [51]:
sample_text, sample_labels = next(iter(validation_data))
print("Text batch shape: ", sample_text.shape)
print("Label batch shape: ", sample_labels.shape)
print("First text example: ", sample_text[0])
print("First label example: ", sample_labels[0])

Text batch shape:  (64, 19)
Label batch shape:  (64,)
First text example:  tf.Tensor(
[   3   86    5   29  274  527    2    4   33 2749   13    3  191    7
   12  108 3286    0    0], shape=(19,), dtype=int64)
First label example:  tf.Tensor(2, shape=(), dtype=int64)


パディングに 0 を使用し、語彙外 (OOV) トークンに 1 を使用するため、語彙のサイズが 2 つ増えました。

In [52]:
vocab_size += 2

以前と同じように、パフォーマンスを向上させるためにデータセットを構成します。

In [53]:
train_data = configure_dataset(train_data)
validation_data = configure_dataset(validation_data)

### モデルをトレーニングする

以前と同じように、このデータセットでモデルをトレーニングできます。

In [54]:
model = create_model(vocab_size=vocab_size, num_labels=3)

model.compile(
    optimizer='adam',
    loss=losses.SparseCategoricalCrossentropy(from_logits=True),
    metrics=['accuracy'])

history = model.fit(train_data, validation_data=validation_data, epochs=3)

Epoch 1/3


      1/Unknown - 22s 22s/step - loss: 1.0935 - accuracy: 0.4844

     15/Unknown - 22s 4ms/step - loss: 1.0591 - accuracy: 0.4292

     32/Unknown - 22s 3ms/step - loss: 1.0370 - accuracy: 0.4038

     51/Unknown - 22s 3ms/step - loss: 1.0025 - accuracy: 0.4577

...

634/697 [==========================>...] - ETA: 0s - loss: 0.1886 - accuracy: 0.9283

653/697 [===========================>..] - ETA: 0s - loss: 0.1878 - accuracy: 0.9286

672/697 [===========================>..] - ETA: 0s - loss: 0.1868 - accuracy: 0.9292

690/697 [============================>.] - ETA: 0s - loss: 0.1865 - accuracy: 0.9294

697/697 [==============================] - 3s 4ms/step - loss: 0.1862 - accuracy: 0.9295 - val_loss: 0.4152 - val_accuracy: 0.8382


In [55]:
loss, accuracy = model.evaluate(validation_data)

print("Loss: ", loss)
print("Accuracy: {:2.2%}".format(accuracy))

      1/Unknown - 1s 603ms/step - loss: 0.4481 - accuracy: 0.8438

     27/Unknown - 1s 2ms/step - loss: 0.3972 - accuracy: 0.8414  

     54/Unknown - 1s 2ms/step - loss: 0.4058 - accuracy: 0.8409

79/79 [==============================] - 1s 2ms/step - loss: 0.4152 - accuracy: 0.8382


Loss:  0.41523823142051697
Accuracy: 83.82%


### モデルをエクスポートする

モデルが生の文字列を入力として受け取ることができるようにするには、カスタム前処理関数と同じ手順を実行する `TextVectorization` レイヤーを作成します。すでに語彙をトレーニングしているので、新しい語彙をトレーニングする `TextVectorization.adapt` の代わりに、`TextVectorization.set_vocabulary` を使用できます。

In [56]:
preprocess_layer = TextVectorization(
    max_tokens=vocab_size,
    standardize=tf_text.case_fold_utf8,
    split=tokenizer.tokenize,
    output_mode='int',
    output_sequence_length=MAX_SEQUENCE_LENGTH)

preprocess_layer.set_vocabulary(vocab)

/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/numpy/core/numeric.py:2468: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  return bool(asarray(a1 == a2).all())
/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/keras/layers/preprocessing/index_lookup.py:458: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  if self.mask_token is not None and self.mask_token in tokens:


In [57]:
export_model = tf.keras.Sequential(
    [preprocess_layer, model,
     layers.Activation('sigmoid')])

export_model.compile(
    loss=losses.SparseCategoricalCrossentropy(from_logits=False),
    optimizer='adam',
    metrics=['accuracy'])

In [58]:
# Create a test dataset of raw strings.
test_ds = all_labeled_data.take(VALIDATION_SIZE).batch(BATCH_SIZE)
test_ds = configure_dataset(test_ds)

loss, accuracy = export_model.evaluate(test_ds)

print("Loss: ", loss)
print("Accuracy: {:2.2%}".format(accuracy))

2022-12-15 01:18:17.427116: W tensorflow/core/grappler/optimizers/loop_optimizer.cc:907] Skipping loop optimization for Merge node with control input: sequential_4/text_vectorization_2/UnicodeScriptTokenize/Assert_1/AssertGuard/branch_executed/_185


      1/Unknown - 5s 5s/step - loss: 0.7075 - accuracy: 0.7344

      8/Unknown - 5s 7ms/step - loss: 0.5362 - accuracy: 0.7734

     16/Unknown - 5s 7ms/step - loss: 0.5461 - accuracy: 0.7852

     24/Unknown - 5s 7ms/step - loss: 0.5640 - accuracy: 0.7773

...

     64/Unknown - 6s 7ms/step - loss: 0.5714 - accuracy: 0.7786

     71/Unknown - 6s 7ms/step - loss: 0.5681 - accuracy: 0.7779

     78/Unknown - 6s 7ms/step - loss: 0.5733 - accuracy: 0.7764

79/79 [==============================] - 6s 7ms/step - loss: 0.5736 - accuracy: 0.7764


Loss:  0.5736407041549683
Accuracy: 77.64%


エンコードされた検証セットのモデルと生の検証セットのエクスポートされたモデルの損失と正確度は、予想どおり同じです。

### 新しいデータで推論を実行する

In [59]:
inputs = [
    "Join'd to th' Ionians with their flowing robes,",  # Label: 1
    "the allies, and his armour flashed about him so that he seemed to all",  # Label: 2
    "And with loud clangor of his arms he fell.",  # Label: 0
]

predicted_scores = export_model.predict(inputs)
predicted_labels = tf.math.argmax(predicted_scores, axis=1)

for input, label in zip(inputs, predicted_labels):
  print("Question: ", input)
  print("Predicted label: ", label.numpy())

2022-12-15 01:18:20.841752: W tensorflow/core/grappler/optimizers/loop_optimizer.cc:907] Skipping loop optimization for Merge node with control input: sequential_4/text_vectorization_2/UnicodeScriptTokenize/Assert_1/AssertGuard/branch_executed/_185


Question:  Join'd to th' Ionians with their flowing robes,
Predicted label:  1
Question:  the allies, and his armour flashed about him so that he seemed to all
Predicted label:  2
Question:  And with loud clangor of his arms he fell.
Predicted label:  0


## TensorFlow Datasets (TFDS) を使用して、より多くのデータセットをダウンロードする


[TensorFlow Dataset](https://www.tensorflow.org/datasets/catalog/overview) からより多くのデータセットをダウンロードできます。

この例では、[IMDB 大規模映画レビューデータセット](https://www.tensorflow.org/datasets/catalog/imdb_reviews)を使用して、感情分類のモデルをトレーニングします。

In [60]:
# Training set.
train_ds = tfds.load(
    'imdb_reviews',
    split='train[:80%]',
    batch_size=BATCH_SIZE,
    shuffle_files=True,
    as_supervised=True)

In [61]:
# Validation set.
val_ds = tfds.load(
    'imdb_reviews',
    split='train[80%:]',
    batch_size=BATCH_SIZE,
    shuffle_files=True,
    as_supervised=True)

いくつかの例を出力します。

In [62]:
for review_batch, label_batch in val_ds.take(1):
  for i in range(5):
    print("Review: ", review_batch[i].numpy())
    print("Label: ", label_batch[i].numpy())

Review:  b"Instead, go to the zoo, buy some peanuts and feed 'em to the monkeys. Monkeys are funny. People with amnesia who don't say much, just sit there with vacant eyes are not all that funny.<br /><br />Black comedy? There isn't a black person in it, and there isn't one funny thing in it either.<br /><br />Walmart buys these things up somehow and puts them on their dollar rack. It's labeled Unrated. I think they took out the topless scene. They may have taken out other stuff too, who knows? All we know is that whatever they took out, isn't there any more.<br /><br />The acting seemed OK to me. There's a lot of unfathomables tho. It's supposed to be a city? It's supposed to be a big lake? If it's so hot in the church people are fanning themselves, why are they all wearing coats?"
Label:  0
Review:  b'Well, was Morgan Freeman any more unusual as God than George Burns? This film sure was better than that bore, "Oh, God". I was totally engrossed and LMAO all the way through. Carrey was

これで、以前と同じようにデータを前処理してモデルをトレーニングできます。

注意: これは二項分類の問題であるため、モデルには `tf.keras.losses.SparseCategoricalCrossentropy` の代わりに  `tf.keras.losses.BinaryCrossentropy` を使用します。

### トレーニング用データセットを準備する

In [63]:
vectorize_layer = TextVectorization(
    max_tokens=VOCAB_SIZE,
    output_mode='int',
    output_sequence_length=MAX_SEQUENCE_LENGTH)

# Make a text-only dataset (without labels), then call `TextVectorization.adapt`.
train_text = train_ds.map(lambda text, labels: text)
vectorize_layer.adapt(train_text)

In [64]:
def vectorize_text(text, label):
  text = tf.expand_dims(text, -1)
  return vectorize_layer(text), label

In [65]:
train_ds = train_ds.map(vectorize_text)
val_ds = val_ds.map(vectorize_text)

In [66]:
# Configure datasets for performance as before.
train_ds = configure_dataset(train_ds)
val_ds = configure_dataset(val_ds)

### モデルを作成、構成、およびトレーニングする

In [67]:
model = create_model(vocab_size=VOCAB_SIZE + 1, num_labels=1)
model.summary()

Model: "sequential_5"


_________________________________________________________________


 Layer (type)                Output Shape              Param #   


 embedding_2 (Embedding)     (None, None, 64)          640064    


 conv1d_2 (Conv1D)           (None, None, 64)          20544     


...

 dense_3 (Dense)             (None, 1)                 65        


Total params: 660,673


Trainable params: 660,673


Non-trainable params: 0


_________________________________________________________________


In [68]:
model.compile(
    loss=losses.BinaryCrossentropy(from_logits=True),
    optimizer='adam',
    metrics=['accuracy'])

In [69]:
history = model.fit(train_ds, validation_data=val_ds, epochs=3)

Epoch 1/3


  1/313 [..............................] - ETA: 28:06 - loss: 0.6936 - accuracy: 0.5156

 14/313 [>.............................] - ETA: 1s - loss: 0.6935 - accuracy: 0.4866   

 28/313 [=>............................] - ETA: 1s - loss: 0.6923 - accuracy: 0.4944

 43/313 [===>..........................] - ETA: 0s - loss: 0.6911 - accuracy: 0.5011

...

256/313 [=======================>......] - ETA: 0s - loss: 0.1963 - accuracy: 0.9237

271/313 [========================>.....] - ETA: 0s - loss: 0.1947 - accuracy: 0.9240

286/313 [==========================>...] - ETA: 0s - loss: 0.1921 - accuracy: 0.9254

301/313 [===========================>..] - ETA: 0s - loss: 0.1894 - accuracy: 0.9270

313/313 [==============================] - 1s 4ms/step - loss: 0.1885 - accuracy: 0.9276 - val_loss: 0.3167 - val_accuracy: 0.8624


In [70]:
loss, accuracy = model.evaluate(val_ds)

print("Loss: ", loss)
print("Accuracy: {:2.2%}".format(accuracy))

 1/79 [..............................] - ETA: 3s - loss: 0.2385 - accuracy: 0.8906

27/79 [=========>....................] - ETA: 0s - loss: 0.3132 - accuracy: 0.8663

53/79 [===================>..........] - ETA: 0s - loss: 0.3166 - accuracy: 0.8611

79/79 [==============================] - 0s 2ms/step - loss: 0.3167 - accuracy: 0.8624


Loss:  0.3166657090187073
Accuracy: 86.24%


### モデルをエクスポートする

In [71]:
export_model = tf.keras.Sequential(
    [vectorize_layer, model,
     layers.Activation('sigmoid')])

export_model.compile(
    loss=losses.SparseCategoricalCrossentropy(from_logits=False),
    optimizer='adam',
    metrics=['accuracy'])

In [72]:
# 0 --> negative review
# 1 --> positive review
inputs = [
    "This is a fantastic movie.",
    "This is a bad movie.",
    "This movie was so bad that it was good.",
    "I will never say yes to watching this movie.",
]

predicted_scores = export_model.predict(inputs)
predicted_labels = [int(round(x[0])) for x in predicted_scores]

for input, label in zip(inputs, predicted_labels):
  print("Question: ", input)
  print("Predicted label: ", label)

Question:  This is a fantastic movie.
Predicted label:  1
Question:  This is a bad movie.
Predicted label:  0
Question:  This movie was so bad that it was good.
Predicted label:  0
Question:  I will never say yes to watching this movie.
Predicted label:  1


## まとめ

このチュートリアルでは、テキストを読み込んで前処理するいくつかの方法を示しました。次のステップとして、以下のような [TensorFlow Text](https://www.tensorflow.org/text) テキスト前処理 チュートリアルをご覧ください。

- [TF テキストを使用した BERT 前処理](https://www.tensorflow.org/text/guide/bert_preprocessing_guide)
- [TF Text を使用したトークン化](https://www.tensorflow.org/text/guide/tokenizers)
- [サブワードトークナイザー](https://www.tensorflow.org/text/guide/subwords_tokenizer)

[TensorFlow Datasets](https://www.tensorflow.org/datasets/catalog/overview) でも新しいデータセットを見つけることができます。また、`tf.data` の詳細については、[入力パイプラインの構築](../../guide/data.ipynb)に関するガイドをご覧ください。